<a href="https://colab.research.google.com/github/pratap977/CS6910/blob/main/CNN_updated.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install split-folders

In [2]:
!pip install wandb

     |████████████████████████████████| 1.7 MB 7.1 MB/s 
     |████████████████████████████████| 181 kB 87.2 MB/s 
     |████████████████████████████████| 144 kB 63.5 MB/s 
     |████████████████████████████████| 63 kB 2.1 MB/s 
  Created wheel for pathtools: filename=pathtools-0.1.2-py3-none-any.whl size=8806 sha256=6cc151450dbd55538d3270860cabf32dfd46e00bbd86cb5f39af8782932ea57b
  Stored in directory: /root/.cache/pip/wheels/3e/31/09/fa59cef12cdcfecc627b3d24273699f390e71828921b2cbba2
Successfully built pathtools


In [3]:
import numpy as np
import tensorflow as tf
from tensorflow import keras
import math as mh
from matplotlib import pyplot
from tensorflow.keras.layers import Conv2D,MaxPooling2D,Activation,Dense,Flatten
from keras.preprocessing.image import load_img as im
from keras.preprocessing.image import save_img as sim
import os
from random import shuffle
import numpy as np
import splitfolders
from PIL import Image
from torchvision import transforms
from tensorflow.keras.preprocessing import image
from tensorflow.keras import layers,models
import wandb
import pathlib
# import torch

In [ ]:
data_folders="/content/inaturalist_12K/train"

In [ ]:
splitfolders.ratio(data_folders, output="outputfin", seed=1337, ratio=(.9, .1), group_prefix=None)

Copying files: 9999 files [00:11, 855.67 files/s]


In [5]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!rm -rf /content/drive/MyDrive/outputfin

In [ ]:
!cp -r /content/outputfin /content/drive/MyDrive/

In [ ]:
!rm -rf nature_12K.zip

In [ ]:
!rm -rf inaturalist_12K/train

In [7]:
#gettig labels for different classes and assigning values
class_labels = os.listdir("/content/drive/MyDrive/outputfin/train")
lab={l:i for l,i in zip(class_labels,range(10))}




##############################################################
#function for prepating data takes two parameters
#1.drive_path - path to drive i.e training or validataion or test
#2.want_aug - Takes 'YES' or 'NO' values to gather info wheter to augment data or not
def prepare_data(drive_path,want_aug):
  imgs_tr = []
  truth_tr = []
  #data augmentation rules here
  data_augmentation  = transforms.Compose([
          transforms.CenterCrop(224),
          transforms.ToTensor(),
          transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
      ])
  for l in class_labels:
    #### for each folder in the val dir we iterate though all the files 
    if l.startswith("."):
      continue
    imgs_per_class = os.listdir(os.path.join(drive_path, l)) #getting list of file names
    for img in imgs_per_class:
      #iterating to each file in the folder 
      img_path = os.path.join(drive_path, l, img)
      img=Image.open(img_path)
      img = img.resize((224,224))
      if img.mode == 'L':
                  continue
      if(want_aug=='YES'):
        normalized_image = data_augmentation(img)
        imgs_tr.append(np.asarray(normalized_image).transpose(1,2,0))
      else:
        normalized_image = img
        imgs_tr.append(np.asarray(normalized_image))
      truth_tr.append(lab[l])
      
  #contain augmented images(imgs_tr) and labels(truth_tr)
  return np.asarray(imgs_tr) , np.asarray(truth_tr) 



#####################################################################
# Preparing training set (with augmentation), validation set and test test
####################################################################
# Preparing training data with augmentation
# Loading data from directory


#############augmented Training data############ 
x_train,y_train=prepare_data("/content/drive/MyDrive/outputfin/train",'YES')


#############augmented validation data############ 
x_val,y_val=prepare_data("/content/drive/MyDrive/outputfin/val",'YES')

#############augmented test data############
x_test,y_test=prepare_data("/content/drive/MyDrive/inaturalist_12K/val",'YES')




#####################################################################
# Preparing training set (without augmentation), validation set and test test
####################################################################
# Preparing training data withou augmentation
# Loading data from directory
#############augmented Training data############ 
x_train_un,y_train_un=prepare_data("/content/drive/MyDrive/outputfin/train",'NO')


#############augmented validation data############ 
x_val_un,y_val_un=prepare_data("/content/drive/MyDrive/outputfin/val",'NO')

#############augmented test data############
x_test_un,y_test_un=prepare_data("/content/drive/MyDrive/inaturalist_12K/val",'NO')




In [12]:
class_labels

['Animalia',
 'Plantae',
 'Aves',
 'Fungi',
 'Mammalia',
 'Arachnida',
 'Mollusca',
 'Reptilia',
 'Insecta',
 'Amphibia']

In [13]:
lab

{'Amphibia': 9,
 'Animalia': 0,
 'Arachnida': 5,
 'Aves': 2,
 'Fungi': 3,
 'Insecta': 8,
 'Mammalia': 4,
 'Mollusca': 6,
 'Plantae': 1,
 'Reptilia': 7}

In [15]:
x_train_un.shape,y_train_un.shape,x_val_un.shape,y_val_un.shape,x_test_un.shape,y_test_un.shape

((8997, 224, 224, 3),
 (8997,),
 (999, 224, 224, 3),
 (999,),
 (2000, 224, 224, 3),
 (2000,))

In [16]:
x_train.shape,y_train.shape,x_val.shape,y_val.shape,x_test.shape,y_test.shape

((8997, 224, 224, 3),
 (8997,),
 (999, 224, 224, 3),
 (999,),
 (2000, 224, 224, 3),
 (2000,))

In [8]:
sweep_config = {
                  'method'    : "bayes",
                  'metric':{
                            'name':'val_accuracy',
                            'goal':'maximize'
                            },
                  'parameters': {
                                  'flt'                 : {'values' :[32, 64,16,]  },
                                  'filterorg'               : {'values' :[1,2,0.5] },
                                  'kerneldim'               : {'values' :[3,4,5,7,2]  },
                                  'activation'              : {'values' :['sigmoid','relu','tanh','elu'] },
                                  'neurons'                 : {'values' :[20,32,64,128,512,1024] },
                                  'optimizer'               : {'values' :['adam'] },
                                  'lr'                      : {'values' :[1e-3,1e-4,2e-3,3e-3,4e-3,3e-4] },
                                  'epochs'                  : {'values' :[20,25,30,35] },
                                  'batchsize'               : {'values' :[16,32,64,128] },
                                  'dropout'                 : {'values' :[0.2,0.25,0.3,0,0.1,0.5,0.6] },
                                  'batchnormalisation'       : {'values' :['YES','NO']} ,
                                  'augmentation' : {'values':['YES','NO']},
                                 }
                }

In [9]:
def create_CNN(fil,ker,activ,batchnormalisation,dropout,neurons):
  cnn=models.Sequential()
  cnn.add(layers.Conv2D(filters=fil[0], kernel_size=(ker[0], ker[0]), activation='relu',input_shape=(224, 224, 3)))
  cnn.add(layers.MaxPooling2D((2, 2)))
  if(batchnormalisation=='YES'):
    cnn.add(layers.BatchNormalization())
        
        
  cnn.add(layers.Conv2D(filters=fil[1], kernel_size=(ker[1], ker[1]), activation='relu'))
  cnn.add(layers.MaxPooling2D((2, 2)))
  if(batchnormalisation=='YES'):
    cnn.add(layers.BatchNormalization())
                                                  
  cnn.add(layers.Conv2D(filters=fil[2], kernel_size=(ker[2], ker[2]), activation='relu'))
  cnn.add(layers.MaxPooling2D((2, 2)))
  if(batchnormalisation=='YES'):
    cnn.add(layers.BatchNormalization())
         
  cnn.add(layers.Conv2D(filters=fil[3], kernel_size=(ker[3], ker[3]), activation='relu'))
  cnn.add(layers.MaxPooling2D((2, 2)))
  if(batchnormalisation=='YES'):
    cnn.add(layers.BatchNormalization())

  cnn.add(layers.Conv2D(filters=fil[4], kernel_size=(ker[4], ker[4]), activation='relu'))
  cnn.add(layers.MaxPooling2D((2, 2)))
  
  if(batchnormalisation=='YES'):
    cnn.add(layers.BatchNormalization())


  cnn.add(layers.Flatten())
  if(dropout!=0):
    cnn.add(layers.Dropout(dropout))
  cnn.add(layers.Dense(neurons, activation=activ))
  
  cnn.add(layers.Dense(10, activation='softmax'))
  return cnn

In [ ]:
cnn=create_CNN([16,8,4,2,1],[5,5,5,5,5],'relu','YES',0.5,20)

In [10]:
cnn=create_CNN([32,64,128,256,512],[5,5,5,5,5],'relu','YES',0.2,20)

In [14]:
cnn.compile(optimizer= tf.keras.optimizers.RMSprop(learning_rate=0.003),
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])
# cnn.fit(train_data, batch_size=128,epochs=10,validation_data=val_data)
cnn.fit(x_train,y_train, batch_size=128,epochs=1,validation_data=(x_val,y_val))

71/71 [==============================] - 25s 204ms/step - loss: 4.1729 - accuracy: 0.1313 - val_loss: 6.4190 - val_accuracy: 0.0991


In [15]:
#best model 1
cnn1=create_CNN([64,128,256,512,1024],[3,3,3,3,3],'sigmoid','NO',0.5,32)
cnn1.compile(optimizer= tf.keras.optimizers.Adam(learning_rate=0.0001),
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])
# cnn.fit(train_data, batch_size=128,epochs=10,validation_data=val_data)
cnn1.fit(x_train,y_train, batch_size=16,epochs=35,validation_data=(x_val,y_val))
tloss,tacc=cnn1.evaluate(x_test,y_test)
  # wandb.log({"Test loss":tloss,"Test Accuracy":tacc})
print("Test loss:",tloss,"Test Accuracy:",tacc)

Epoch 1/35
563/563 [==============================] - 34s 44ms/step - loss: 2.1841 - accuracy: 0.1933 - val_loss: 2.1152 - val_accuracy: 0.2272
Epoch 2/35
563/563 [==============================] - 23s 42ms/step - loss: 2.0692 - accuracy: 0.2690 - val_loss: 2.0771 - val_accuracy: 0.2633
Epoch 3/35
563/563 [==============================] - 23s 42ms/step - loss: 2.0052 - accuracy: 0.2981 - val_loss: 1.9911 - val_accuracy: 0.2953
Epoch 4/35
563/563 [==============================] - 23s 42ms/step - loss: 1.9599 - accuracy: 0.3200 - val_loss: 1.9545 - val_accuracy: 0.3143
Epoch 5/35
563/563 [==============================] - 23s 42ms/step - loss: 1.9125 - accuracy: 0.3314 - val_loss: 1.9340 - val_accuracy: 0.3053
Epoch 6/35
563/563 [==============================] - 23s 41ms/step - loss: 1.8668 - accuracy: 0.3567 - val_loss: 1.8897 - val_accuracy: 0.3333
Epoch 7/35
563/563 [==============================] - 23s 41ms/step - loss: 1.8250 - accuracy: 0.3779 - val_loss: 1.8735 - val_accuracy:

In [18]:
# Saving the model
cnn1.save(pathlib.Path('/content/drive/MyDrive/DL_Assignment2_PartA_Model1'))

NameError: ignored

In [19]:
# Loading the saved model (Also required for Q4 (b), Q4 (c) and Q5)
cnn1 = tf.keras.models.load_model(pathlib.Path('/content/drive/MyDrive/DL_Assignment2_PartA_Model1'))
tloss,tacc=cnn1.evaluate(x_test,y_test)
# wandb.log({"Test loss":tloss,"Test Accuracy":tacc})
print("Test loss:",tloss,"Test Accuracy:",tacc)

63/63 [==============================] - 2s 29ms/step - loss: 1.8954 - accuracy: 0.4305
Test loss: 1.8954236507415771 Test Accuracy: 0.43050000071525574


In [21]:
x_test.shape

(2000, 224, 224, 3)

In [22]:
#best model 2
cnn1=create_CNN([64,128,256,512,1024],[3,3,3,3,3],'sigmoid','NO',0.5,128)
cnn1.compile(optimizer= tf.keras.optimizers.Adam(learning_rate=0.0003),
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])
# cnn.fit(train_data, batch_size=128,epochs=10,validation_data=val_data)
cnn1.fit(x_train,y_train, batch_size=16,epochs=35,validation_data=(x_val,y_val))
tloss,tacc=cnn1.evaluate(x_test,y_test)
# wandb.log({"Test loss":tloss,"Test Accuracy":tacc})
print("Test loss:",tloss,"Test Accuracy:",tacc)

Epoch 1/35
563/563 [==============================] - 27s 46ms/step - loss: 2.1681 - accuracy: 0.2028 - val_loss: 2.0941 - val_accuracy: 0.2422
Epoch 2/35
563/563 [==============================] - 25s 45ms/step - loss: 2.0194 - accuracy: 0.2791 - val_loss: 1.9423 - val_accuracy: 0.3063
Epoch 3/35
563/563 [==============================] - 25s 45ms/step - loss: 1.9129 - accuracy: 0.3263 - val_loss: 1.8614 - val_accuracy: 0.3243
Epoch 4/35
563/563 [==============================] - 25s 45ms/step - loss: 1.8044 - accuracy: 0.3710 - val_loss: 1.7815 - val_accuracy: 0.3784
Epoch 5/35
563/563 [==============================] - 25s 45ms/step - loss: 1.6996 - accuracy: 0.4104 - val_loss: 1.7605 - val_accuracy: 0.3874
Epoch 6/35
563/563 [==============================] - 25s 44ms/step - loss: 1.5790 - accuracy: 0.4546 - val_loss: 1.7494 - val_accuracy: 0.3814
Epoch 7/35
563/563 [==============================] - 25s 45ms/step - loss: 1.4215 - accuracy: 0.5097 - val_loss: 1.7273 - val_accuracy:

In [23]:
# Saving the model
cnn1.save(pathlib.Path('/content/drive/MyDrive/DL_Assignment2_PartA_Model2'))

INFO:tensorflow:Assets written to: /content/drive/MyDrive/DL_Assignment2_PartA_Model2/assets


In [20]:
# Loading the saved model (Also required for Q4 (b), Q4 (c) and Q5)
cnn1 = tf.keras.models.load_model(pathlib.Path('/content/drive/MyDrive/DL_Assignment2_PartA_Model2'))
tloss,tacc=cnn1.evaluate(x_test,y_test)

63/63 [==============================] - 2s 29ms/step - loss: 3.1484 - accuracy: 0.4065


In [24]:
#best model 3
cnn1=create_CNN([32,64,128,256,512],[7,7,7,7,7],'sigmoid','YES',0.25,512)
cnn1.compile(optimizer= tf.keras.optimizers.Adam(learning_rate=0.0003),
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])
# cnn.fit(train_data, batch_size=128,epochs=10,validation_data=val_data)
cnn1.fit(x_train,y_train, batch_size=128,epochs=35,validation_data=(x_val,y_val))
tloss,tacc=cnn1.evaluate(x_test,y_test)
# wandb.log({"Test loss":tloss,"Test Accuracy":tacc})
print("Test loss:",tloss,"Test Accuracy:",tacc)

Epoch 1/35
71/71 [==============================] - 20s 237ms/step - loss: 2.0544 - accuracy: 0.2693 - val_loss: 2.1873 - val_accuracy: 0.1902
Epoch 2/35
71/71 [==============================] - 18s 248ms/step - loss: 1.8855 - accuracy: 0.3351 - val_loss: 2.3794 - val_accuracy: 0.1582
Epoch 3/35
71/71 [==============================] - 18s 247ms/step - loss: 1.7942 - accuracy: 0.3660 - val_loss: 2.4121 - val_accuracy: 0.1782
Epoch 4/35
71/71 [==============================] - 18s 247ms/step - loss: 1.6992 - accuracy: 0.4022 - val_loss: 2.1129 - val_accuracy: 0.2623
Epoch 5/35
71/71 [==============================] - 17s 247ms/step - loss: 1.5967 - accuracy: 0.4421 - val_loss: 1.8652 - val_accuracy: 0.3574
Epoch 6/35
71/71 [==============================] - 18s 248ms/step - loss: 1.4882 - accuracy: 0.4898 - val_loss: 1.8011 - val_accuracy: 0.3594
Epoch 7/35
71/71 [==============================] - 18s 248ms/step - loss: 1.3288 - accuracy: 0.5478 - val_loss: 1.8806 - val_accuracy: 0.3654

In [25]:
# Saving the model
cnn1.save(pathlib.Path('/content/drive/MyDrive/DL_Assignment2_PartA_Model3'))

INFO:tensorflow:Assets written to: /content/drive/MyDrive/DL_Assignment2_PartA_Model3/assets


In [21]:
# Loading the saved model (Also required for Q4 (b), Q4 (c) and Q5)
cnn1 = tf.keras.models.load_model(pathlib.Path('/content/drive/MyDrive/DL_Assignment2_PartA_Model3'))
tloss,tacc=cnn1.evaluate(x_test,y_test)

63/63 [==============================] - 2s 23ms/step - loss: 2.5389 - accuracy: 0.4020


In [26]:
#best model 1
cnn1=create_CNN([64,128,256,512,1024],[3,3,3,3,3],'sigmoid','NO',0.5,32)
cnn1.compile(optimizer= tf.keras.optimizers.Adam(learning_rate=0.0001),
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])
# cnn.fit(train_data, batch_size=128,epochs=10,validation_data=val_data)
cnn1.fit(x_train,y_train, batch_size=16,epochs=10,validation_data=(x_test,y_test))
tloss,tacc=cnn1.evaluate(x_val,y_val)
  # wandb.log({"Test loss":tloss,"Test Accuracy":tacc})
print("Test loss:",tloss,"Test Accuracy:",tacc)

Epoch 1/10
563/563 [==============================] - 26s 45ms/step - loss: 2.1747 - accuracy: 0.2130 - val_loss: 2.2967 - val_accuracy: 0.1345
Epoch 2/10
563/563 [==============================] - 24s 43ms/step - loss: 2.0503 - accuracy: 0.2771 - val_loss: 2.2837 - val_accuracy: 0.1335
Epoch 3/10
563/563 [==============================] - 24s 43ms/step - loss: 2.0077 - accuracy: 0.2969 - val_loss: 2.2221 - val_accuracy: 0.1940
Epoch 4/10
563/563 [==============================] - 24s 43ms/step - loss: 1.9656 - accuracy: 0.3164 - val_loss: 2.2962 - val_accuracy: 0.1600
Epoch 5/10
563/563 [==============================] - 24s 43ms/step - loss: 1.9262 - accuracy: 0.3326 - val_loss: 2.2355 - val_accuracy: 0.1860
Epoch 6/10
563/563 [==============================] - 24s 43ms/step - loss: 1.8772 - accuracy: 0.3601 - val_loss: 2.3002 - val_accuracy: 0.1545
Epoch 7/10
563/563 [==============================] - 24s 43ms/step - loss: 1.8408 - accuracy: 0.3721 - val_loss: 2.3750 - val_accuracy:

In [18]:
def conlay():
  wandb.init(config=sweep_config, magic=True)  
  f= wandb.config.flt 
  fo=  wandb.config.filterorg                           
  fil=[ (int)(f*(fo)**i) if((int)(f*(fo)**i)>0) else  1 for i in range(5)]
  kd=wandb.config.kerneldim
  ker=[kd for i in range(5)]
  if(wandb.config.activation=="sigmoid"):
    activ=tf.keras.activations.sigmoid
  elif(wandb.config.activation=="tanh"):
    activ=tf.keras.activations.tanh
  elif(wandb.config.activation=="relu"):
    activ='relu'
  else:
    activ=tf.keras.activations.elu
  if(wandb.config.optimizer=="sgd"):
    optim = tf.keras.optimizers.SGD(learning_rate=wandb.config.lr)
  elif(wandb.config.optimizer=="adam"):
    optim = tf.keras.optimizers.Adam(learning_rate=wandb.config.lr)
  elif(wandb.config.optimizer=="momentum"):
    optim = tf.keras.optimizers.SGD(learning_rate=wandb.config.lr,momentum=wandb.config.gama)
  elif(wandb.config.optimizer=="rmsprop"):
    optim = tf.keras.optimizers.RMSprop(learning_rate=wandb.config.lr)
      
  cnn =create_CNN(fil,ker,activ,wandb.config.batchnormalisation,wandb.config.dropout,wandb.config.neurons)             
  cnn.compile(optimizer=optim,
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])
  if(wandb.config.augmentation=='YES'):
    cnn.fit(x_train, y_train, batch_size=wandb.config.batchsize,epochs=wandb.config.epochs,validation_data=(x_val,y_val),callbacks=[tf.keras.callbacks.EarlyStopping(monitor = 'val_accuracy', patience = 5),
                                            wandb.keras.WandbCallback()])
    tloss,tacc=cnn.evaluate(x_val,y_val)
  # wandb.log({"Test loss":tloss,"Test Accuracy":tacc})
    #print("Test loss:",tloss,"Test Accuracy:",tacc)
  else:
    cnn.fit(x_train_un, y_train_un, batch_size=wandb.config.batchsize,epochs=wandb.config.epochs,validation_data=(x_val_un,y_val_un),callbacks=[tf.keras.callbacks.EarlyStopping(monitor = 'val_accuracy', patience = 5),
                                            wandb.keras.WandbCallback()])
    tloss,tacc=cnn.evaluate(x_val_un,y_val_un)
  wandb.log({"Test loss":tloss,"Test Accuracy":tacc})
  del cnn


In [19]:
wandb.login()


<IPython.core.display.Javascript object>

wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

In [20]:
sweep_id = wandb.sweep(sweep_config,project='A2-part-A1')
wandb.agent(sweep_id,conlay,project='A2-part-A1')

Create sweep with ID: 99pl6u2g
Sweep URL: https://wandb.ai/pratap49/A2-part-A1/sweeps/99pl6u2g


wandb: Agent Starting Run: emwqblsc with config:
wandb: 	activation: sigmoid
wandb: 	batchnormalisation: NO
wandb: 	batchsize: 32
wandb: 	dropout: 0
wandb: 	epochs: 35
wandb: 	filterorg: 0.5
wandb: 	flt: 16
wandb: 	kerneldim: 3
wandb: 	lr: 0.003
wandb: 	neurons: 128
wandb: 	optimizer: adam
wandb: Currently logged in as: pratap49 (use `wandb login --relogin` to force relogin)


Epoch 1/35
282/282 [==============================] - 7s 21ms/step - loss: 2.3218 - accuracy: 0.1124 - val_loss: 2.3199 - val_accuracy: 0.1281 - _timestamp: 1648853092.0000 - _runtime: 17.0000
Epoch 2/35
282/282 [==============================] - 5s 18ms/step - loss: 2.2800 - accuracy: 0.1336 - val_loss: 2.2469 - val_accuracy: 0.1682 - _timestamp: 1648853097.0000 - _runtime: 22.0000
Epoch 3/35
282/282 [==============================] - 5s 18ms/step - loss: 2.2135 - accuracy: 0.1695 - val_loss: 2.2092 - val_accuracy: 0.1612 - _timestamp: 1648853102.0000 - _runtime: 27.0000
Epoch 4/35
282/282 [==============================] - 5s 19ms/step - loss: 2.1653 - accuracy: 0.1910 - val_loss: 2.1716 - val_accuracy: 0.2022 - _timestamp: 1648853107.0000 - _runtime: 32.0000
Epoch 5/35
282/282 [==============================] - 5s 18ms/step - loss: 2.1494 - accuracy: 0.2030 - val_loss: 2.1691 - val_accuracy: 0.2052 - _timestamp: 1648853112.0000 - _runtime: 37.0000
Epoch 6/35
282/282 [===============

wandb: Agent Starting Run: g93nm53j with config:
wandb: 	activation: sigmoid
wandb: 	batchnormalisation: YES
wandb: 	batchsize: 16
wandb: 	dropout: 0.5
wandb: 	epochs: 35
wandb: 	filterorg: 0.5
wandb: 	flt: 32
wandb: 	kerneldim: 3
wandb: 	lr: 0.0003
wandb: 	neurons: 32
wandb: 	optimizer: adam


Epoch 1/35
563/563 [==============================] - 11s 17ms/step - loss: 2.3640 - accuracy: 0.1186 - val_loss: 2.2384 - val_accuracy: 0.1762 - _timestamp: 1648853297.0000 - _runtime: 19.0000
Epoch 2/35
563/563 [==============================] - 8s 15ms/step - loss: 2.2216 - accuracy: 0.1785 - val_loss: 2.1601 - val_accuracy: 0.2162 - _timestamp: 1648853306.0000 - _runtime: 28.0000
Epoch 3/35
563/563 [==============================] - 9s 15ms/step - loss: 2.1723 - accuracy: 0.1964 - val_loss: 2.1222 - val_accuracy: 0.2362 - _timestamp: 1648853314.0000 - _runtime: 36.0000
Epoch 4/35
563/563 [==============================] - 9s 15ms/step - loss: 2.1494 - accuracy: 0.2065 - val_loss: 2.0947 - val_accuracy: 0.2452 - _timestamp: 1648853323.0000 - _runtime: 45.0000
Epoch 5/35
563/563 [==============================] - 9s 16ms/step - loss: 2.1378 - accuracy: 0.2100 - val_loss: 2.0753 - val_accuracy: 0.2563 - _timestamp: 1648853332.0000 - _runtime: 54.0000
Epoch 6/35
563/563 [==============

...

Run ejzai8rx errored: ResourceExhaustedError()
wandb: ERROR Run ejzai8rx errored: ResourceExhaustedError()
wandb: Agent Starting Run: of9nyzl4 with config:
wandb: 	activation: relu
wandb: 	batchnormalisation: NO
wandb: 	batchsize: 32
wandb: 	dropout: 0
wandb: 	epochs: 30
wandb: 	filterorg: 2
wandb: 	flt: 16
wandb: 	kerneldim: 3
wandb: 	lr: 0.0001
wandb: 	neurons: 20
wandb: 	optimizer: adam


Run of9nyzl4 errored: ResourceExhaustedError()
wandb: ERROR Run of9nyzl4 errored: ResourceExhaustedError()
wandb: Agent Starting Run: y3x70084 with config:
wandb: 	activation: sigmoid
wandb: 	batchnormalisation: NO
wandb: 	batchsize: 128
wandb: 	dropout: 0
wandb: 	epochs: 35
wandb: 	filterorg: 2
wandb: 	flt: 16
wandb: 	kerneldim: 5
wandb: 	lr: 0.002
wandb: 	neurons: 128
wandb: 	optimizer: adam


Run y3x70084 errored: ResourceExhaustedError()
wandb: ERROR Run y3x70084 errored: ResourceExhaustedError()
wandb: Agent Starting Run: 5a7viuj5 with config:
wandb: 	activation: sigmoid
wandb: 	batchnormalisation: YES
wandb: 	batchsize: 32
wandb: 	dropout: 0.25
wandb: 	epochs: 35
wandb: 	filterorg: 2
wandb: 	flt: 64
wandb: 	kerneldim: 5
wandb: 	lr: 0.004
wandb: 	neurons: 64
wandb: 	optimizer: adam


Run 5a7viuj5 errored: ResourceExhaustedError()
wandb: ERROR Run 5a7viuj5 errored: ResourceExhaustedError()
wandb: Agent Starting Run: chx8hyac with config:
wandb: 	activation: relu
wandb: 	batchnormalisation: YES
wandb: 	batchsize: 32
wandb: 	dropout: 0.2
wandb: 	epochs: 20
wandb: 	filterorg: 1
wandb: 	flt: 16
wandb: 	kerneldim: 5
wandb: 	lr: 0.002
wandb: 	neurons: 20
wandb: 	optimizer: adam


Run chx8hyac errored: ResourceExhaustedError()
wandb: ERROR Run chx8hyac errored: ResourceExhaustedError()
wandb: Sweep Agent: Waiting for job.
wandb: Job received.
wandb: Agent Starting Run: rncrnw8s with config:
wandb: 	activation: tanh
wandb: 	batchnormalisation: YES
wandb: 	batchsize: 64
wandb: 	dropout: 0.5
wandb: 	epochs: 20
wandb: 	filterorg: 1
wandb: 	flt: 32
wandb: 	kerneldim: 4
wandb: 	lr: 0.0003
wandb: 	neurons: 20
wandb: 	optimizer: adam
Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.


In [ ]:
def conlayss():
  # wandb.init(config=sweep_config, magic=True)    
  cnn = models.Sequential([
                     
    layers.Conv2D(32, kernel_size=(3,3), activation='relu', input_shape=(224, 224, 3)),
    layers.MaxPooling2D((2,2)),
    
    layers.Conv2D(64,  kernel_size=(3,3), activation='relu'),
    layers.MaxPooling2D((2,2)),

    layers.Conv2D(64, kernel_size=(3,3), activation='relu'),
    layers.MaxPooling2D((2,2)),

    layers.Conv2D(64,  kernel_size=(3,3), activation='relu'),
    layers.MaxPooling2D((2,2)),

    layers.Conv2D(64,  kernel_size=(3,3), activation='relu'),
    layers.MaxPooling2D((2,2)),
    layers.Flatten(),
    layers.Dropout(0.2),

    
    layers.Dense(30, activation='relu'),
    layers.Dense(10, activation='softmax')
  ])
  #gc.collect()
  # heyGPU=torch.cuda.is_available()
  # if heyGPU: cnnModel=cnnModel.cuda()
  print("start")
  train_dataset = tf.data.Dataset.from_tensor_slices((x_train, y_train))
  train_dataset = train_dataset.shuffle(buffer_size=1024).batch(64)

    # Prepare the validation dataset.
  val_dataset = tf.data.Dataset.from_tensor_slices((x_val, y_val))
  val_dataset = val_dataset.batch(64)
  print("end")
  cnn.compile(optimizer='adam',
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])
  cnn.fit(train_dataset,val_dataset,batch_size=64 ,epochs=10)
  del cnn
  # torch.cuda.empty_cache()

In [ ]:
y_train[5]

0

In [ ]:
conlayss()

start


InternalError: ignored

In [ ]:
import torch

#denormalizaImg function de augument the image provided as parameter to it and returns the de deaugmented pic 
def denormalizeImg(pic):
  mu, sd = [0.485, 0.456, 0.406], [0.229, 0.224, 0.225]
  good = pic.cpu() * torch.tensor(sd).view(3, 1, 1).cpu() + torch.tensor(mu).view(3, 1, 1)
  img = transforms.ToPILImage(mode='RGB')(good)
  return img

#This function is used to accumulate 30 test pics from x_test where for each Image we gather 2 images i.e augmented and deaugmented Image
#Function returns a list of lists where each inner list contains augmented and deaugmented Image for a particular image
def getImages():
  data=[]
  for i in lab:
    k=0
    for j in len(x_test):
      if(k==3):
        break
      if(y_test[j]==lab[i]):
        de=denormalizeImg(x_test)
        data.append([x_test,de])
        k+=1
  return data



In [11]:
class_lables

NameError: ignored